In [ ]:
import openmc
import numpy as np
import matplotlib.pyplot as plt

# Quick Note On Syntax / Getters & Setters

In [ ]:
# this:
my_material1 = openmc.Material()
my_material1.name = 'first material!'

# is equivalent to this:
my_material2 = openmc.Material(name='second first material!')

## you can access an object property with object.property
print(my_material2.name)

## either initalizing with properties or setting a property later (with a built in fuction or with object.property = value) both do the same thing
# in this guide, for readability, I'll use the built in functions or object.property = value most of the time, but it's not the only way

# Materials

In [ ]:
## make material
fuel = openmc.Material()

## name
fuel.name = "fuel material"

#### Add nuclides

In [ ]:
## add nuclide (nuclide, percent, percent type)
fuel.add_nuclide(nuclide='U235', percent=0.025, percent_type='ao')
# this is equivelant:
fuel.add_nuclide('U238', 0.475, 'ao')
# print(fuel)

- nuclide specifies the nuclide
- percent specifies how much of the total material will be that nuclide
- percent type specifies if the percent is atom% or weight%"

#### Add elements

In [ ]:
# add element (element, percent, percent type)
fuel.add_element(element='O', percent=0.5, percent_type='ao')

same as add_nuclide, except it adds an entire element with natural isotopic abundance

#### Set density

In [ ]:
# set density (atom / barn-cm) vs (g/cc)
fuel.set_density(units="g/cm3", density=8.00)

#### Set temperature

In [ ]:
## set temperature
fuel.temperature = 900 # K

Note: there is no built in function to set the temperature ( ie. set_temperature() ), you just set it with oject.property = value

#### View the Material

In [ ]:
## view the material
print(fuel)

notes:
- the id is automatically set for OpenMC to keep track of things
- even though you put O in as an element, OpenMC automatically breakes it down into isotopes using the natural abundnaces

#### Adding TSLs

In [ ]:
water = openmc.Material(name = "water")
water.add_element('O', 1/3, 'ao')
water.add_element('H', 2/3, 'ao')
water.set_density("g/cm3", 1)
water.temperature = 298 # K

In [ ]:
## Assign the h_in_h2o tsl to the material 'water'
water.add_s_alpha_beta('c_H_in_H2O')

#### U235 Enrichment Function

In [ ]:
uo2 = openmc.Material(name = "fuel material")
uo2.add_element('U', percent=0.5, percent_type='ao', enrichment=0.049)
uo2.add_element(element='O', percent=0.5, percent_type='ao')
uo2.set_density(units="g/cm3", density=8.00)
uo2.temperature = 900 # K

#### Export to xml

In [ ]:
## Export to xml
my_materials = openmc.Materials([uo2, water])
my_materials.export_to_xml()

# Surfaces

#### Spheres

In [ ]:
## Sphere initalization
my_first_sphere = openmc.Sphere() # https://docs.openmc.org/en/stable/pythonapi/generated/openmc.Sphere.html#openmc.Sphere

## Sphere paramaters
# we can set an origin and a radius.
# default origin is (x=0,y=0,z=0)
my_first_sphere.r = 5
# r has units of cm

# print(my_first_sphere)

#### Cylinders

In [ ]:
## With Cylinders, we have 3 options: an X, Y, or Z cylinder
# each is an infinite cylinder with the axial direction being the one indicated (X, Y, or Z)

## Cylinder initlization
my_first_z_cylinder = openmc.ZCylinder() # https://docs.openmc.org/en/stable/pythonapi/generated/openmc.ZCylinder.html#openmc.ZCylinder

## Cylinder paramaters
# we can set an origin for the center of the Cylinder in the x-y plane
# default origin is (x=0,y=0)
# we can not an origin in 3d space because this is an infinite cylinder in the z direction
# we can also set the radius of the Cylinder
my_first_z_cylinder.r = 2
# r has units of cm

# print(my_first_z_cylinder)

#### Planes

In [ ]:
## with planes, there are 4 options: X, Y, Z, and general
# the general is more complicate, so we will stick with just X, Y, and Z
# Each plane is an infinite flat plane normal to the specified axis

## Plane initlization
my_first_x_plane = openmc.XPlane() # https://docs.openmc.org/en/stable/pythonapi/generated/openmc.XPlane.html#openmc.XPlane
my_second_x_plane = openmc.XPlane() # https://docs.openmc.org/en/stable/pythonapi/generated/openmc.XPlane.html#openmc.XPlane
my_first_y_plane = openmc.YPlane()
my_second_y_plane = openmc.YPlane()

## Plane paramaters
# we can only set the offset from the origin on these
my_first_x_plane.x0 = 3
my_second_x_plane.x0 = -3

my_first_y_plane.x0 = 3
my_second_y_plane.x0 = -3

# print(my_second_y_plane)

#### Half Spaces
Each equation is written and can be viewed at [The OpenMC Documentation Website](https://docs.openmc.org/en/stable/usersguide/geometry.html)

The "surface" is the locations where the equation evalueates to 0.

Everywhere else, the equation will evaluate to either a + or a - value.

These spaces are called half-spaces, and they are how we specify what our geometry is.

For example, all points **inside** a sphere evaluate to a negative number when applied to the equation, so the negative half space of a sphere is the area inside the sphere.

This is critical to understand when creating models, so please take time to wrap your head around it.

Note:
- For cylinders and spheres: - is inside and + is outside
- For Planes: + is in the + direction and - is in the - direction of the plane

In [ ]:
## given a sphere:
my_sphere = openmc.Sphere()
my_sphere.r = 10 # cm

## the half space is denoted by putting a + or a - in front of your surface
inside_sphere = -my_sphere
outside_sphere = +my_sphere

#### Combining Half Spaces
Half Spaces can be combined using Boolean operators.

The operators allowed are the following:
- & (intersection, can be considered as the AND operator)
- | (union, can be considered as the OR operator)
- ~ (compliment, can be considered as the NOT operator)

I almost always use the & operator. Pretty much any shape can be made with that operator, and it is the most intuitive. Also, often under the hood, the code reduces the operators down to & operators anyway.

A note: We don't often write out the combination of half spaces until the creation of a cell, this is just for conceptual understandind

In [ ]:
## If I want to create cylinder that is 1cm in radius, and 10 cm tall I could do the following:
my_Zcylinder = openmc.ZCylinder()
my_Zcylinder.r = 1 # cm (note, the origin in the xy plane is by default (x=0, y=0) )

my_topZplane = openmc.ZPlane()
my_topZplane.z0 = -5 # cm
my_bottomZplane = openmc.ZPlane()
my_bottomZplane.z0 = 5 # cm

my_rod = -my_Zcylinder & +my_bottomZplane & -my_topZplane

#### Boundary Conditions

Every surface has a boundary condition. Anytime a particle reaches the boundary of a surface, it checks the boundary condition before proceeding. A couple things can happen:
- if the boundary is "transmission" (which every surface is by default, and most surfaces will be), the particle continues in the same direction with the same energy
- if the boundary is "vacuum", the particle is terminated
- if the boundary is "reflective", the particle will be bounced back with the oppostite direction and the same energy as before
- the boundary can also be "periodic" or a number of other options, but we won't talk about those for now

In [ ]:
## For the most outer surface, if you want to set the bounary to be a vacuum:
outer_sphere = openmc.Sphere()
outer_sphere.r = 20 # cm
outer_sphere.boundary_type='vacuum'

# Cells
A cell is a region that is defined in space (using half-space intersections) with an associated material to fill it.
#### Note:
- fill requires a material
- region requires a half space or the intersection of a number of half spaces

In [ ]:
## If I wanted to creat a cell that is only the top half of the previous sphere:
z0_plane = openmc.ZPlane(z0 = 0)

top_half_of_fuel_cell = openmc.Cell()
top_half_of_fuel_cell.fill = fuel
top_half_of_fuel_cell.region = -my_sphere & +z0_plane

In [ ]:
# Make Some More Surfaces To Use Here
S10 = openmc.Sphere()
S10.r = 10
S10.boundary_type='vacuum'
Z0 = openmc.ZPlane()
Z0.z0 = 0

In [ ]:
# Cells
top_cell = openmc.Cell(fill = uo2)
top_cell.region = -S10 & +Z0
bottom_cell = openmc.Cell(fill = water)
bottom_cell.region = -S10 & -Z0

# Universes

### In order to create a base universe and export geometry to xml:
1. Create a "main universe" (named whatever you want) of the object type "Universe" with a value of your cells in list form (note: you don't export surfaces, only cells)
2. Create the openmc object "Geometry" with a value of your "main universe"
3. Export that object to xml

**Note: There can be nested universes, and universes can also have the option to be a fill for a cell. That's not shown here.**

In [ ]:
my_universe = openmc.Universe(cells = [bottom_cell, top_cell])
my_geometry = openmc.Geometry(my_universe)
my_geometry.export_to_xml()

In [ ]:
## visualize this cell in the xy plane
my_universe.plot(width=(20.0, 20.0), basis='xy')

In [ ]:
## visualize this cell in the xz plane
my_universe.plot(width=(20.0, 20.0), basis='xz')

# Sources

In [ ]:
## If I want to make a point source at the location (x=0, y=0, z=1)

## first create the point as an openmc object using the openmc.stats module
source_point = openmc.stats.Point((0, 0, 1))

## Then create the source object using openmc.IndependentSource. Input the source point you just created
my_point_source = openmc.IndependentSource(space = source_point)

In [ ]:
## If I want to make a box source of specified paramaters

source_box = openmc.stats.Box(
lower_left  = (-1.0, -1.0, -1.0),
upper_right = ( 1.0,  1.0,  1.0)
)
my_box_source = openmc.IndependentSource(space = source_box)

# Settings

# Create settings, and export them to xml
- only create minimum required settings (run_mode, particles, batches, inactive cycles, source), but there are many more

### In order to create settings:
1. Create a "settings" object
2. Specify settings paramaters
3. Export settings object to xml

In [ ]:
## inital "settings" object
my_settings = openmc.Settings()

# this run mode calculates keff
my_settings.run_mode = 'eigenvalue'

# normally you would run with more particles, but while testing on your local computer, run with a small amount of particles
my_settings.particles = 1000

# this will run with 100 active cycles and 50 inactive cycles
my_settings.batches   = 150
my_settings.inactive  = 50

# input the previous source objec into your settings
my_settings.source = my_point_source

## once all settings are specified, export them to the xml
my_settings.export_to_xml()

# Tallies
Create energy bins to seperate tallies into (ie. count a neutron in bin n if it has energy between $E_n$ and $E_{n+1}$).

Create Tallies to calculate:
- Flux
- Total Reaction Rate
- Fission Rate
- Absorption Rate

In [ ]:
## create the bins for the energy filter as a list in python to input into the OpenMC energy filter object
my_bins = [1e-5, 1e-4, 1e-3, 1e-2, 1e-1, 1e-0, 1e1, 1e2, 1e3, 1e4, 1e5, 1e6, 1e7, 1e8, 1e9]

In [ ]:
material_filter = openmc.MaterialFilter([fuel]) # filter to only count neutrons in the fuel material
energy_filter = openmc.EnergyFilter(my_bins) # energy filter based on bins we created

In [ ]:
## Note: we name the tallies so that later in post-processing we can more easily access them

## Tally Flux
flux_tally = openmc.Tally(name="flux")
flux_tally.filters = [material_filter, energy_filter]
flux_tally.scores = ['flux']

## Tally Fission Rate
fission_tally = openmc.Tally(name="fission")
fission_tally.filters = [material_filter, energy_filter]
fission_tally.scores = ['fission']

In [ ]:
## create tallies.xml
tallies = openmc.Tallies([flux_tally, fission_tally])
tallies.export_to_xml()

#### **NOTE: tallies will need to be post processed: an example of that will be shown in the MCFR-D example notebook**